In [1]:
#Importa as bibliotecas necessárias
import pandas as pd
import numpy as np
import datetime
from datetime import timedelta
import random
import math

#Ignora os avisos de possíveis mudanças nas bibliotecas utilizadas
import warnings
warnings.simplefilter("ignore")

# Base Colaboradores Fictícia

In [2]:
#Define os horários de entrada fictícios
entradas = [str(i)+':00' for i in range(0,24)]

#Cria um dataframe que incluirá as informações de quantos colaboradores devem iniciar o trabalho em cada horário, aos dias úteis, sábados e domingos
df_requeridos = pd.DataFrame({'entrada':entradas})

#Cria uma função que define o número de colaboradores iniciando em cada horário, dando peso maior ao horário comercial e menor aos horários da madrugada
def define_requeridos(entrada):
  aleatorio = random.randint(0,40)
  if int(entrada[:-3])<6:
    requeridos = math.ceil(aleatorio/8)
  elif int(entrada[:-3])<19:
    requeridos = aleatorio
  else:
    requeridos = math.ceil(aleatorio/2)

  return requeridos

#Define os requeridos para cada dia, com a utilização da função criada anteriormente. Aos sábados e domingos, o número será uma fração pré-definida
#do que é para os dias úteis
df_requeridos['requeridos_dia_util'] = list(map(define_requeridos,df_requeridos['entrada']))
df_requeridos['requeridos_sabado'] = df_requeridos['requeridos_dia_util'].apply(lambda entrada: math.ceil(entrada*0.70))
df_requeridos['requeridos_domingo'] = df_requeridos['requeridos_dia_util'].apply(lambda entrada: int(entrada*0.30))

#Cria um dicionário que tem como chaves os horários de entrada, e como valores o número de funcionários contratados para cada horário
funcionarios = {}
for i in df_requeridos.index:
  #Para o exemplo atual, para se aproximar do cenário real - que quase nunca é o ideal -, foi decidido implementar uma certa aleatoriedade no número de
  #funcionários em cada horário. Esse número pode variar de -1 a +1 o número de requeridos para cada horário
  funcionarios[df_requeridos.iloc[i,0]] = random.randint(df_requeridos.iloc[i,1]-1, df_requeridos.iloc[i,1]+1)

df_requeridos['colaboradores'] = df_requeridos['entrada'].apply(lambda entrada: funcionarios[entrada])

#Ilustra a forma final do dataframe
display(df_requeridos.head())

#Apresenta o número total de requeridos em cada dia e o número total de funcionários disponíveis
df_requeridos.sum()

entrada  requeridos_dia_util  requeridos_sabado  requeridos_domingo  \
0    0:00                    1                  1                   0   
1    1:00                    4                  3                   1   
2    2:00                    1                  1                   0   
3    3:00                    1                  1                   0   
4    4:00                    1                  1                   0   

   colaboradores  
0              1  
1              5  
2              0  
3              2  
4              1

entrada                0:001:002:003:004:005:006:007:008:009:0010:001...
requeridos_dia_util                                                  380
requeridos_sabado                                                    274
requeridos_domingo                                                   106
colaboradores                                                        380
dtype: object

In [3]:
#Cria uma base fictícia de colaboradores, representados por suas matrículas únicas
base_ficticia = pd.DataFrame()
#Seleciona uma amostra de códigos de matrícula com quantia equivalente ao número de colaboradores disponíveis
base_ficticia['matricula'] = random.sample(range(100,999),df_requeridos['colaboradores'].sum())

In [4]:
#Define os horários de entrada (em mesmo número para cada horário que o indicdo no "df_requeridos", coluna "colaboradores") dos colaboradore da base fictícia 
entrada_colaboradores = []

for i in df_requeridos.index:
  lista_temp = df_requeridos.iloc[i,4]*[df_requeridos.iloc[i,0]]
  entrada_colaboradores = entrada_colaboradores + lista_temp

#Aleatoriza os horários de entrada dos colaboradores 
random.shuffle(entrada_colaboradores)
base_ficticia['entrada'] = pd.Series(entrada_colaboradores).apply(lambda entrada: pd.to_datetime(entrada).time())
base_ficticia.sort_values(by='entrada', inplace = True)

base_ficticia

matricula   entrada
294        805  00:00:00
223        877  01:00:00
74         154  01:00:00
234        259  01:00:00
345        775  01:00:00
..         ...       ...
41         959  23:00:00
31         305  23:00:00
14         945  23:00:00
365        782  23:00:00
268        783  23:00:00

[380 rows x 2 columns]

#Histórico de domingos trabalhados fictício

In [5]:
#Cria um histórico fictício da situação do último domingo. Neste caso, foi utilizado como exemplo que o último domingo foi dia 08/01/2023
df_historico = pd.DataFrame(base_ficticia['matricula'])
df_historico['data'] = pd.to_datetime('2023-01-08').date()
#Define aleatoriamente quem trabalhou no último domingo, seguindo a proporção definida inicialmente (70% sábado - 30% domingo)
df_historico['tipo'] = ["Trabalha" if random.randint(1,10) < 4 else "Folga" for i in range(len(base_ficticia))]

display(df_historico)

df_historico['tipo'].value_counts()

matricula        data      tipo
294        805  2023-01-08     Folga
223        877  2023-01-08  Trabalha
74         154  2023-01-08     Folga
234        259  2023-01-08  Trabalha
345        775  2023-01-08  Trabalha
..         ...         ...       ...
41         959  2023-01-08  Trabalha
31         305  2023-01-08     Folga
14         945  2023-01-08  Trabalha
365        782  2023-01-08     Folga
268        783  2023-01-08     Folga

[380 rows x 3 columns]

Folga       279
Trabalha    101
Name: tipo, dtype: int64

# Escala de folga

In [6]:
#Definição de quem obrigatoriamente trabalhará no próximo sábado (todos que já trabalharam no domingo anterior)
ultimo_domingo = max(df_historico['data'])
sabado_obrigatorio = base_ficticia[base_ficticia['matricula'].isin(df_historico[(df_historico['data'] == ultimo_domingo) & 
                                                                                (df_historico['tipo'] == 'Trabalha') ]['matricula'])]

In [7]:
#Define o número de pessoas que devem trabalhar no sábado e no domingo
colaboradores_sabado = df_requeridos['requeridos_sabado'].sum()
colaboradores_domingo = df_requeridos['requeridos_domingo'].sum()

print(colaboradores_sabado,'\n',colaboradores_domingo)


274 
 106


In [9]:
#Define os colaboradores restantes - que ainda não possuem dia de trabalho definido
colaboradores_restantes = base_ficticia[base_ficticia['matricula'].isin(sabado_obrigatorio['matricula']) == False]

#Define a proporção de colaboradores, em relação aos restantes, que devem logar no domingo.
proporcao_domingo_sabado = colaboradores_domingo/(colaboradores_sabado+colaboradores_domingo-len(sabado_obrigatorio))

#Define o número de colaboradores que trabalharão domingo
sorteio_domingo = math.ceil(proporcao_domingo_sabado*len(colaboradores_restantes))

#Define aleatoriamente quem trabalhará sábado e domingo, dentre os colaboradores restantes
lista_colaboradores_restantes = list(colaboradores_restantes['matricula'])
random.shuffle(lista_colaboradores_restantes)
trabalha_domingo = base_ficticia[base_ficticia['matricula'].isin(lista_colaboradores_restantes[:sorteio_domingo])]
trabalha_sabado = base_ficticia[base_ficticia['matricula'].isin(lista_colaboradores_restantes[:sorteio_domingo]) == False]

trabalha_sabado.sort_values(by='entrada', inplace = True)
trabalha_domingo.sort_values(by='entrada', inplace = True)

In [ ]:
#Cria uma função que ajusta os horários dos finais de semana, de acordo com o número de colaboradores total em cada dia
def ajusta_horarios(df_trabalha,colaboradores_dia,dia):

  if dia == 'sab':
    coluna = 2
  else:
    coluna = 3

  saldo = len(df_trabalha) - colaboradores_dia

  #Se houver menos colaboradores do que o requerido, deve-se indicar que haverá déficit. Nesse caso, cria-se colaboradores fictícios até que se
  #atinja o número de colaboradores requeridos, para definição prévia dos horários de entrada em expediente
  if saldo < 0:

    entrada_dia = []
    for i in df_requeridos.index:
      lista_temp = df_requeridos.iloc[i,coluna]*[df_requeridos.iloc[i,0]]
      entrada_dia = entrada_dia + lista_temp

    colaboradores_ficticios = pd.DataFrame()
    colaboradores_ficticios['matricula'] = ['ficticio' for i in range(abs(saldo))]
    colaboradores_ficticios['entrada'] = [pd.to_datetime(random.sample(entradas,1)[0]).time() for i in range(abs(saldo))]
    df_trabalha = pd.concat([df_trabalha,colaboradores_ficticios], axis = 0)
    df_trabalha.sort_values(by='entrada', inplace=True)  
    df_trabalha.reset_index(inplace = True, drop = True)

    df_trabalha['entrada_escala'] = pd.Series(entrada_dia).apply(lambda entrada: pd.to_datetime(entrada).time())

  #Caso haja um número maior de colaboradores em algum dia do que os requeridos, deve-se criar horários adicionais para adequar todos. Estes 
  #são definidos aleatoriamente
  elif saldo > 0:

    novo_df_requeridos = df_requeridos.copy()
    
    for i in range(saldo):
      aleatorio = random.randint(0,23)
      novo_df_requeridos.iloc[aleatorio,coluna] = novo_df_requeridos.iloc[aleatorio,coluna] + 1

    entrada_dia = []
    for i in novo_df_requeridos.index:
      lista_temp = novo_df_requeridos.iloc[i,coluna]*[novo_df_requeridos.iloc[i,0]]
      entrada_dia = entrada_dia + lista_temp

    df_trabalha.sort_values(by='entrada', inplace=True)  
    df_trabalha.reset_index(inplace = True, drop = True)

    df_trabalha['entrada_escala'] = pd.Series(entrada_dia).apply(lambda entrada: pd.to_datetime(entrada).time())

  #Caso o número de colaboradores seja equivalente ao de requeridos, é necessário apenas distribuir os horários já existentes
  else:
    entrada_dia = []
    for i in df_requeridos.index:
      lista_temp = df_requeridos.iloc[i,coluna]*[df_requeridos.iloc[i,0]]
      entrada_dia = entrada_dia + lista_temp

    df_trabalha.sort_values(by='entrada', inplace=True)  
    df_trabalha.reset_index(inplace = True, drop = True)

    df_trabalha['entrada_escala'] = pd.Series(entrada_dia).apply(lambda entrada: pd.to_datetime(entrada).time())

  return df_trabalha

In [ ]:
#Define os horários de entrada para cada dia utilizando a função criada e unifica ambos em um único dataframe
trabalha_sabado = ajusta_horarios(trabalha_sabado,colaboradores_sabado,'sab')
trabalha_sabado['dia_trabalho'] = 'Sábado'
trabalha_domingo = ajusta_horarios(trabalha_domingo,colaboradores_domingo,'dom')
trabalha_domingo['dia_trabalho'] = 'Domingo'
df_escala = pd.concat([trabalha_sabado,trabalha_domingo], axis = 0)
df_escala.sort_values(by = 'entrada_escala', inplace = True)

<ipython-input-11-ee381b7050bb>:59: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_trabalha['entrada_escala'] = pd.Series(entrada_dia).apply(lambda entrada: pd.to_datetime(entrada).time())
<ipython-input-12-c52eb55711a4>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  trabalha_domingo['dia_trabalho'] = 'Domingo'


In [ ]:
#Para seguir as normas regulatórias, deve-se estabelecer um horário de entrada de escala com no máximo 2h de diferença em relação ao
#horário regular. A função a seguir realiza esse ajusta para os casos que incialmente ultrapassem esse limite
def corrige_entrada_escala(entrada_escala, entrada):
  diferenca_entrada = entrada_escala.hour - entrada.hour

  if diferenca_entrada < -2:
    entrada_escala = pd.to_datetime(str(entrada.hour-2)+':00').time()
  elif diferenca_entrada > 2:
    entrada_escala = pd.to_datetime(str(entrada.hour+2)+':00').time()

  return entrada_escala

#Realiza o ajuste dos horários de entrada
df_escala['entrada_escala'] = list(map(corrige_entrada_escala,df_escala['entrada_escala'],df_escala['entrada']))
#Elimina os colaboradores fictícios
df_escala = df_escala[df_escala['matricula'] != 'ficticio']

# Atualiza histórico de domingos trabalhados

In [ ]:
#Prepara a nova escala para inclusão no registro de domingos trabalhados
df_registro = df_escala[['matricula','dia_trabalho']]
df_registro['data'] = ultimo_domingo + timedelta(days=7)

<ipython-input-14-c36a5a385a57>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_registro['data'] = ultimo_domingo + timedelta(days=7)


In [ ]:
#Cria uma função que informa se o domingo foi de trabalho ou de usufruto de folga
def trabalha_data(dia_trabalho):
  if dia_trabalho == 'Sábado':
    tipo = 'Folga'
  else:
    tipo = 'Trabalha'

df_registro['tipo'] = list(map(trabalha_data,df_registro['dia_trabalho']))
df_registro.drop(columns='dia_trabalho', inplace = True)

#Inclui a nova escala ao registro já existente
df_historico = pd.concat([df_historico,df_registro],axis = 0)

# Define se haverá déficit ou sobras na escala

In [ ]:
#Prepara um dataframe para análise de excedentes ou déficit em relação aos requeridos totais (acumulado de todos os horários)
df_requeridos_acumulados = df_requeridos.drop(columns = 'colaboradores')

In [ ]:
#Cria uma função para somar os requeridos das últimas seis horas, para definir os requeridos acumulados
def acumula_requeridos(df_coluna_anterior, df_coluna):
  acumulado = [df_coluna[indice-5:indice+1].sum() if indice >= 5 else df_coluna[:indice+1].sum() + df_coluna_anterior[19+indice:].sum() for indice in range(24)]

  return acumulado

#Executa a função criada para cada um dos dias da escala
df_requeridos_acumulados['sabado'] = acumula_requeridos(df_requeridos_acumulados['requeridos_dia_util'],df_requeridos_acumulados['requeridos_sabado'])
df_requeridos_acumulados['domingo'] = acumula_requeridos(df_requeridos_acumulados['requeridos_sabado'],df_requeridos_acumulados['requeridos_domingo'])
df_requeridos_acumulados['dia_util'] = acumula_requeridos(df_requeridos_acumulados['requeridos_domingo'],df_requeridos_acumulados['requeridos_dia_util'])

In [ ]:
#Cria um dataframe que incluirá os acumulados reais em cada horário, de acordo com a escala elaborada
df_acumulado_real = pd.DataFrame({'entrada':entradas})
#Inclui no dataframe o número de colaboradores que iniciam o expediente em cada horário de cada dia, de acordo com a escala
df_acumulado_real['dia_util'] = df_acumulado_real['entrada'].apply(lambda entrada: len(df_escala[df_escala['entrada'] == pd.to_datetime(entrada).time()]))
df_acumulado_real['sabado'] = df_acumulado_real['entrada'].apply(lambda entrada: len(df_escala[(df_escala['entrada'] == pd.to_datetime(entrada).time()) & 
                                                                                                (df_escala['dia_trabalho'] == 'Sábado')]))
df_acumulado_real['domingo'] = df_acumulado_real['entrada'].apply(lambda entrada: len(df_escala[(df_escala['entrada'] == pd.to_datetime(entrada).time()) & 
                                                                                                (df_escala['dia_trabalho'] == 'Domingo')]))
#Inclui no dataframe o acumulado real em cada horário de cada dia, de acordo com a escala
df_acumulado_real['acumulado_sabado'] = acumula_requeridos(df_acumulado_real['dia_util'],df_acumulado_real['sabado'])
df_acumulado_real['acumulado_domingo'] = acumula_requeridos(df_acumulado_real['sabado'],df_acumulado_real['domingo'])
df_acumulado_real['acumulado_dia_util'] = acumula_requeridos(df_acumulado_real['domingo'],df_acumulado_real['dia_util'])

In [ ]:
#Cria um dataframe para análisar expecificamente o déficit ou excedentes em cada horário de cada dia
df_deficit = pd.DataFrame({'entrada':entradas})

#Cria uma função que define o déficit ou excedentes em cada horário de cada dia
def saldo (requeridos, real):
  saldo = real - requeridos

  return saldo

#Aplica a função criada para cada horário de cada dia
df_deficit['segunda'] = list(map(saldo,df_requeridos_acumulados.iloc[:,6],df_acumulado_real.iloc[:,6]))
df_deficit['sabado'] = list(map(saldo,df_requeridos_acumulados.iloc[:,4],df_acumulado_real.iloc[:,4]))
df_deficit['domingo'] = list(map(saldo,df_requeridos_acumulados.iloc[:,5],df_acumulado_real.iloc[:,5]))

In [ ]:
df_deficit

entrada  segunda  sabado  domingo
0     0:00        2       1       -1
1     1:00        0      -1        1
2     2:00       -2      -1        1
3     3:00        1       0        1
4     4:00       -1      -2        3
5     5:00        0      -2        2
6     6:00       -1      -3        2
7     7:00        0       2       -2
8     8:00        0       0        0
9     9:00       -2       2       -4
10   10:00        0       7       -7
11   11:00       -2       5       -7
12   12:00       -2       6       -8
13   13:00       -2       3       -5
14   14:00       -1       6       -7
15   15:00       -1       1       -2
16   16:00       -1      -1        0
17   17:00        0      -3        3
18   18:00        0      -4        4
19   19:00        0      -6        6
20   20:00        0      -8        8
21   21:00        0      -4        4
22   22:00       -1      -6        5
23   23:00        0      -2        2